<a href="https://colab.research.google.com/github/AnnSenina/Python_CL_2023/blob/main/homework/Hw2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Домашнее задание 2

## pandas + парсинг

Здесь находится главная страница [Системного блока](https://sysblok.ru)

Соберите корпус новостей (можно спарсить все новости или небольшую часть)

Дедлайн: 23 декабря включительно

In [1]:
# необходимые импорты
import requests
from bs4 import BeautifulSoup
import pandas as pd

### шаг 1

In [2]:
# соберите все ссылки на страницы с новостями (цикл for + range)
# 1 страница: https://sysblok.ru
# 2 страница: https://sysblok.ru/page/2
# последняя: https://sysblok.ru/page/16

all_pages = ['https://sysblok.ru', ]


for i in range(2,17):
    all_pages.append(f"https://sysblok.ru/page/{i}/")
print(all_pages)


['https://sysblok.ru', 'https://sysblok.ru/page/2/', 'https://sysblok.ru/page/3/', 'https://sysblok.ru/page/4/', 'https://sysblok.ru/page/5/', 'https://sysblok.ru/page/6/', 'https://sysblok.ru/page/7/', 'https://sysblok.ru/page/8/', 'https://sysblok.ru/page/9/', 'https://sysblok.ru/page/10/', 'https://sysblok.ru/page/11/', 'https://sysblok.ru/page/12/', 'https://sysblok.ru/page/13/', 'https://sysblok.ru/page/14/', 'https://sysblok.ru/page/15/', 'https://sysblok.ru/page/16/']


### шаг 2

In [3]:
# с каждой страницы соберите ссылки на отдельные новости
# подсказка: родительский тег h2 (проверяйте по нему), нужный нам - a

all_links = []

for url in all_pages:
    page = requests.get(url)
    soup = BeautifulSoup(page.text, features="html.parser")
    for i in soup.find_all('a'):
        if i.parent.name == 'h2': 
            all_links.append(i.get('href'))
    
all_links = list(set(all_links))
all_links


['https://sysblok.ru/urban/kak-postroit-kartu-vozrastov-zdanij-na-otkrytyh-dannyh-proekt-how-old-is-this-house/',
 'https://sysblok.ru/education/sovremennyj-urok-matematiki-v-cifrovuju-jepohu/',
 'https://sysblok.ru/philology/golos-a-avtora-mozhet-li-odin-chelovek-pisat-kak-neskolko/',
 'https://sysblok.ru/arts/virtualnyj-teatr-vr-spektakli-v-ssha-pozvoljajut-pobyt-otcom-gamleta/',
 'https://sysblok.ru/history/carskie-svitki-i-biografija-konfucija-chto-est-v-korpuse-russkih-perevodov-obshhestvenno-politicheskih-sochinenij-xviii-veka/',
 'https://sysblok.ru/test/kak-horosho-vy-znaete-pesni-korolja-i-shuta/',
 'https://sysblok.ru/philology/data-science-protiv-fejkov-kak-algoritm-otdeljaet-vydumannye-novosti-ot-pravdy/',
 'https://sysblok.ru/arts/muzejnye-tehnologii-i-roboty-v-iskusstve-rasskazyvaem-pro-art-science/',
 'https://sysblok.ru/news/kak-svjazany-nejronnaja-aktivnost-mozga-myshej-i-process-razvoda-suprugov/',
 'https://sysblok.ru/society/tehnologii-budushhego-v-chernom-zerkale/'

### шаг 3

работаем с 1 новостью:

нас интересует название, автор, дата публикации, текст (дополнительно можно спарсить тематические категории)

In [14]:
# для парсинга даты: извлеките текст из тега time
url0 = all_links[0]

page0 = requests.get(url0)
soup0 = BeautifulSoup(page0.text)
time = []
for i in soup0.find_all('time'):
    time.append(i.text)
print(*time, sep = ', ')


20.01.2021, 09.12.2023, 29.11.2023


In [15]:
# для парсинга заголовка: извлеките текст из тега h1
title = []
for x in soup0.find_all('h1'):
    title.append(x.text)
print(*title)

Как построить карту возрастов зданий на открытых данных: проект How old is this house?


In [16]:
# для парсинга текста: соберите все тексты из тега p и соедините в строку
text_list = soup0.find_all('p')
text = [i.text for i in text_list]
final_text = ' '.join(text)
final_text = final_text.replace('\xa0', ' ').replace('\n', ' ')
final_text

'   Визуализация возраста зданий на карте — не новая идея, в том числе для Москвы. Подобную вещь несколько лет назад сделал «Меркатор», сравнительно недавно интерактивную карту опубликовала «Стрелка». Но оба проекта посвящены теме жилищного строительства и показывают только жилые дома. Проект how-old-is-this.house старается показать более полную картину  В основе карты — геометрия зданий из открытых данных Росреестра 2016 года: там высокий уровень детализации, и большинству домов присвоен год постройки. Это и есть ядро проекта. Для актуализации набора использованы данные OpenStreetMap, там гораздо более актуальная информация по сравнению с местами устаревшим Росреестром. Смысловое наполнение карты — названия, стили, данные об архитекторах, фотографии и т.д. — все это взято из открытых данных Министерства культуры, Викимапии и, преимущественно, из портала Wikidata. В итоге получилось 259 тысяч построек, из которых возраст известен у 129 тысяч. Данные о возрасте авторы свели в график: В 

In [7]:
# автора собрать сложнее:
# достаем из тега meta как на паре или из тега a с проверкой на содержимое атрибута rel

author = soup0.find_all('meta', {'name' : 'author'})[0].attrs['content']
print(author)




Милана Глебова


In [18]:
soup0.find_all('a')

[<a class="mauer-narrator-close search-popup-closer" href="#"></a>,
 <a class="logo-link" href="https://sysblok.ru/"> <span class="text-logo">Системный Блокъ</span>
 </a>,
 <a class="logo-link" href="https://sysblok.ru/"> <span class="text-logo">Системный Блокъ</span>
 </a>,
 <a class="search-popup-opener" href=""><i class="icon-search"></i></a>,
 <a class="nav-link" href="https://sysblok.ru/postcards/" title="«Пишу тебе»">«Пишу тебе»</a>,
 <a aria-expanded="false" aria-haspopup="true" class="dropdown-toggle nav-link" data-toggle="dropdown" href="#" id="menu-item-dropdown-215" title="Темы">Темы</a>,
 <a class="dropdown-item" href="https://sysblok.ru/category/nlp/" title="NLP">NLP</a>,
 <a class="dropdown-item" href="https://sysblok.ru/category/biologija/" title="Биология">Биология</a>,
 <a class="dropdown-item" href="https://sysblok.ru/category/visual/" title="Визуализация">Визуализация</a>,
 <a class="dropdown-item" href="https://sysblok.ru/category/oriental/" title="Востоковедение">В

In [26]:
# тематические категории:
# нужные нам категории

#!не смогла разобраться с тематическими категориями, буду еще пытаться

for i in soup0.find_all('a'):
    if i.get('rel') == ['category']:
        print(find_all(i.text))
 


### шаг 4

In [27]:
# пишем функцию по сбору информации

def GetNews(url0):
  page0 = requests.get(url0)
  soup0 = BeautifulSoup(page0.text, features="html.parser")
  author = soup0.find_all('meta', {'name' : 'author'})[0].attrs['content']
  date = soup0.find_all('meta', {'property' : 'article:published_time'})[0].attrs['content']
  title = soup0.find_all('meta', {'property' : 'og:title'})[0].attrs['content']
  text_list = soup0.find_all('p')
  text = [i.text.strip() for i in text_list]
  final_text = ' '.join(text)
  final_text = final_text.replace('\xa0', ' ')
  
  return url0, author, date, title, final_text




In [28]:
# собираем все новости!
# полезно использовать try / except
news = []

for i in all_links:
    try:
        new = GetNews(i)
        news.append(new)
    except:
        print(i)

In [29]:
news

[('https://sysblok.ru/urban/kak-postroit-kartu-vozrastov-zdanij-na-otkrytyh-dannyh-proekt-how-old-is-this-house/',
  'Милана Глебова',
  '2021-01-20T17:00:00+00:00',
  'Как построить карту возрастов зданий на открытых данных: проект How old is this house',
  '  Визуализация возраста зданий на карте — не новая идея, в том числе для Москвы. Подобную вещь несколько лет назад сделал «Меркатор», сравнительно недавно интерактивную карту опубликовала «Стрелка». Но оба проекта посвящены теме жилищного строительства и показывают только жилые дома. Проект how-old-is-this.house старается показать более полную картину В основе карты — геометрия зданий из открытых данных Росреестра 2016 года: там высокий уровень детализации, и большинству домов присвоен год постройки. Это и есть ядро проекта. Для актуализации набора использованы данные OpenStreetMap, там гораздо более актуальная информация по сравнению с местами устаревшим Росреестром. Смысловое наполнение карты — названия, стили, данные об архитек

### шаг 5

In [ ]:
# соберите всю собранную информацию в датафрейм


In [32]:
df = pd.DataFrame(news)
df.columns = ['link', 'author', 'date', 'title', 'text']
df.head()


link              author  \
0  https://sysblok.ru/urban/kak-postroit-kartu-vo...      Милана Глебова   
1  https://sysblok.ru/education/sovremennyj-urok-...    Ульяна Абдуллина   
2  https://sysblok.ru/philology/golos-a-avtora-mo...    Женя Колпащикова   
3  https://sysblok.ru/arts/virtualnyj-teatr-vr-sp...       Даша Масленко   
4  https://sysblok.ru/history/carskie-svitki-i-bi...  Виолетта Арстанова   

                        date  \
0  2021-01-20T17:00:00+00:00   
1  2022-01-19T17:00:00+00:00   
2  2023-08-17T15:00:00+00:00   
3  2020-08-15T17:00:00+00:00   
4  2021-03-23T17:00:36+00:00   

                                               title  \
0  Как построить карту возрастов зданий на открыт...   
1  Как выглядит современный урок математики в шко...   
2  Голос(а) автора: может ли один человек писать ...   
3              Виртуальный театр: VR-спектакли в США   
4  Корпус текстов сочинений о политике и обществе...   

                                                text  
0    Визуализация возраста зданий на карте — не н...  
1    Всеобщая цифровизация повлияла и на школьные...  
2    Стилометрический анализ позволяет определить...  
3    Как технологии виртуальной реальности позвол...  
4    Корпус переводов общественно-политических те...

Готово!
Загрузите ваш код и собранные новости на GitHub